# Fourier Transform

## 1D

### DFT
for a 1D DFT the transform is performed by the following formula:  
$$F(u) = \sum_{x=0}^{N-1}f(x)e^{-\frac{2\pi iux}{N}}$$


In [8]:
import numpy as np
from imageio import imread
from skimage.color import rgb2gray
from scipy.io.wavfile import read, write
from scipy import signal
from scipy.signal import convolve2d as con2d
from scipy.ndimage.interpolation import map_coordinates
from matplotlib import pyplot as plt

IMAGE_FILE = "fox.jpg"
AUDIO_FILE = "commercial-mono.wav"
NUM_BITS = 8

signal = np.array([14, 40, -7,92,3])

def DFT1D(signal):
    # Following the formula above
    N = signal.shape[0]
    x = np.arange(N).reshape(1,N)
    u = x.T
    dft_mat = np.exp(-(2*np.pi*1j*u*x)/N)
    F_sig = np.dot(dft_mat,signal)
    return F_sig

DFT1D(signal)
    

array([142.          +0.j        , -41.47871376 +23.00164887j,
         5.47871376-115.90264945j,   5.47871376+115.90264945j,
       -41.47871376 -23.00164887j])

### iDFT

The inverse-DFT is done using the following formula:  
$$f(x) = \frac{1}{N}\sum_{u=0}^{N-1}F(u)e^{\frac{2\pi iux}{N}}$$

In [9]:
def iDFT1D(signal):
    # Following the formula above
    N = signal.shape[0]
    x = np.arange(N).reshape(1,N)
    u = x.T
    idft_mat = np.exp((2*np.pi*1j*u*x)/N)
    f_sig = np.dot(idft_mat,signal)/N
    return np.real_if_close(f_sig)

iDFT1D(DFT1D(signal))

array([14., 40., -7., 92.,  3.])

## 2D

in 2D the transform goes as follows:
$$F(u) = \sum_{x=0}^{N-1}\sum_{y=0}^{M-1}f(x,y)e^{-2\pi i\left(\frac{ux}{N}+\frac{vy}{M}\right)}$$

We can see that the formula consists of the DFT for each dimension, so we can run the  1D transformation for each row and then in the other axis for each column.  

The same is true for the iDFT: 
$$f(x,y) = \frac{1}{NM}\sum_{u=0}^{N-1}\sum_{v=0}^{M-1}F(u,v)e^{2\pi i\left(\frac{ux}{N}+\frac{vy}{M}\right)}$$

In [10]:
from utils import *

def DFT2D(signal):
    signal=signal.copy()
    F_sig = DFT1D(signal).transpose()
    F_sig = DFT1D(F_sig).transpose()
    return F_sig

def iDFT2D(signal):
    signal=signal.copy()
    f_sig = iDFT1D(signal).transpose()
    f_sig = iDFT1D(f_sig).transpose()
    return np.real_if_close(f_sig)


im = (imread(IMAGE_FILE).astype(np.float64))/((1<<NUM_BITS)-1)
yiq = rgb2yiq(im)
y_ch = (yiq[:,:,0]).copy()

yiq[:,:,0] = DFT2D(y_ch)

figsize,[[ax1,ax2],[ax3,ax4]] = plt.subplots(2,2,figsize = (200,200))
ax1.imshow(im)
ax2.imshow(y_ch,cmap="gray")
ax3.imshow(np.fft.fftshift(np.log(abs(yiq[:,:,0]))), cmap='gray')

# removing first frequencies blurs the image:
blurred=DFT2D(y_ch.copy())
blurred[:850,:590]=np.zeros((850,590))
print(blurred.shape)
ax4.imshow(iDFT2D(blurred).astype(np.float16),cmap="gray")


/tmp/ipykernel_2993413/1950159547.py:20: ComplexWarning: Casting complex values to real discards the imaginary part
  yiq[:,:,0] = DFT2D(y_ch)


(860, 600)


/tmp/ipykernel_2993413/1950159547.py:31: ComplexWarning: Casting complex values to real discards the imaginary part
  ax4.imshow(iDFT2D(blurred).astype(np.float16),cmap="gray")


## Audio manipulation

### Fast forward
#### Change of rate
We can change the speed of an audio file, simply by changing it's sampling rate.
This causes the frequencies to change accordingly, thus changing the pitch.


In [11]:
RATIO = 1.5 # change ratio of the sampling rate
rate, data = read(AUDIO_FILE)

def change_rate(data,rate, ratio):
    rate *= ratio
    write("rate_cange-"+AUDIO_FILE, int(rate), data)

change_rate(data,rate,RATIO)
data.shape

(15769,)

#### Using Fourier transform
we can change the rate of the file by changing the number of samples. this way we keep sampling the data in the same rate as before and still resulting the wanted ratio of length.

We would like to move to the frequency space and remove the highest frequencies, as they have the smallest contribution - they are the sharper changes which resembel noise, or alternatively, add 0 values to higher frequencies in the case of enlarging the samples amount.

    This will not be working very well because the fourier transform is performed globally over all the code, we might want to check the local behavior for better results

In [19]:
def resize_samples(data, ratio):
    f_data = DFT1D(data)
    orig_n_samples = data.shape[0]
    n_samples = int(orig_n_samples / ratio)
    # shift so the lowest frequencies are in the middle
    f_shift = np.fft.fftshift(f_data)
    if ratio > 1:
        #clip
        mid = int(orig_n_samples / 2)
        f_shift = f_shift[mid - int(n_samples / 2):mid + int(n_samples / 2)]
    elif ratio < 1:
        # pad with 0's
        margin = (n_samples - oriorig_n_samples) // 2
        padding = [0] * margin
        f_shift = np.array(padding + list(f_shift) + padding)
    f_shift = np.fft.ifftshift(f_shift) # shift back
    return np.real(iDFT1D(f_shift))

def ff_fourier(data,rate, ratio):
    new_data = resize_samples(data, ratio)
    write("changed-rate-fourier-"+AUDIO_FILE, rate, new_data.astype(np.int16))
    return new_data.astype(np.float64)

rate, data = read(AUDIO_FILE)
print(data.shape,rate)
new_data=ff_fourier(data,rate,RATIO)
print(new_data.shape,rate)

(15769,) 4000
(10512,) 4000


#### Using spectrogram

In order to consider local changes, we would like to divide the data into windows.  Vocoding is used to take in account the phase according to the shift of each window.

In [20]:
from utils import stft,istft,phase_vocoder

def resize_spectrogram(data, ratio):
    four_data = stft(data,1000,400)
    four_data = np.apply_along_axis(resize_samples, 1, four_data, ratio)
    new_data = istft(four_data,1000,400)
    return new_data

rate, data = read(AUDIO_FILE)
write("spectrogram-"+AUDIO_FILE,rate,resize_spectrogram(data,RATIO))

def resize_vocoder(data, ratio):
    f_data = phase_vocoder(stft(data,1000,400), ratio)
    return istft(f_data,1000,400)

rate, data = read(AUDIO_FILE)
write("vocoder-"+AUDIO_FILE,rate,resize_vocoder(data,RATIO))